In [55]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType,ArrayType
from pyspark.sql.functions import split,explode,array,col

In [56]:
spark = SparkSession.builder.appName("PNR").getOrCreate()

In [57]:
df=spark.read.json("pnrf.json", multiLine="True")

In [58]:
df.printSchema()

root
 |-- SabreASDS: struct (nullable = true)
 |    |-- ChangeIndicators: struct (nullable = true)
 |    |    |-- AgencyAccountingData: string (nullable = true)
 |    |    |-- AirExtras: string (nullable = true)
 |    |    |-- ExtFrequentTraveller: string (nullable = true)
 |    |    |-- FQP: string (nullable = true)
 |    |    |-- FirstTransaction: string (nullable = true)
 |    |    |-- FrequentTraveller: string (nullable = true)
 |    |    |-- GeneralFacts: string (nullable = true)
 |    |    |-- HistoryReformatted: string (nullable = true)
 |    |    |-- HostFacts: string (nullable = true)
 |    |    |-- Invoice: string (nullable = true)
 |    |    |-- Itinerary: string (nullable = true)
 |    |    |-- MiscTicketing: string (nullable = true)
 |    |    |-- Name: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- PassengerAddress: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- PassengerDe

In [59]:
def expand_nested_column(df_tmp):
    df = df_tmp
    select_clause_list = []
# Iterating each columns again to check if any next json data is exists
    for name in df.schema.names:
        print("Outside isinstance loop: " + name)
# Checking column type is ArrayType
        if isinstance(df.schema[name].dataType, ArrayType):
            print("Inside isinstance loop: " + name)
#Extracting nested json columns/data using explode function
            df = df.withColumn(name, explode(df.name)).alias(name)
            select_clause_list.append(name)
            #print (select_clause_list)
        elif isinstance(df.schema[name].dataType, StructType):
            print("Inside isinstance loop of StructType: " + name)
            print ("Name is " + name)
            for field in df.schema[name].dataType.fields:
                if isinstance(field.dataType, StructType):
                    select_clause_list.append(name + "." + field.name)
                    #print (select_clause_list)
                    print (field.name)
                else:
                    pass
        else:
            select_clause_list.append(name)
    #print(select_clause_list)
    columnNames = map(lambda x: col(x).alias(x.replace(".","_")), select_clause_list)    # Selecting columns using select_clause_list from dataframe:
    return df.select(*columnNames)

In [60]:
nested_column_count = 1
# Run the while loop until the nested_column_count is zero(0)
while (nested_column_count != 0):
    print("Printing nested_column_count: " + str(nested_column_count))
    nested_column_count_temp = 0
# Iterating each columns again to check if any next json data is exists
    for name in df.schema.names:
        print("Iterating DataFrame Columns: " + name)
# Checking column type is ArrayType
        if isinstance(df.schema[name].dataType, StructType) or isinstance(df.schema[name].dataType, ArrayType):
            nested_column_count_temp += 1
    if (nested_column_count_temp != 0):
        df = expand_nested_column(df)
        df.show(10, False)
    print("Printing nested_column_count_temp: " + str(nested_column_count_temp))
    nested_column_count = nested_column_count_temp

Printing nested_column_count: 1
Iterating DataFrame Columns: SabreASDS
Outside isinstance loop: SabreASDS
Inside isinstance loop of StructType: SabreASDS
Name is SabreASDS
ChangeIndicators
DeltaCalculated
GetReservationRS
PNRSummary
+----------------------------------------------------------------------------------------------------------------------------------------------------------+--------------------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [25]:
spark.stop()